**Copyright 2020 The TensorFlow Authors.**

In [1]:
#@title Licensed under the Apache License, Version 2.0 (the "License");
# you may not use this file except in compliance with the License.
# You may obtain a copy of the License at
#
# https://www.apache.org/licenses/LICENSE-2.0
#
# Unless required by applicable law or agreed to in writing, software
# distributed under the License is distributed on an "AS IS" BASIS,
# WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
# See the License for the specific language governing permissions and
# limitations under the License.

# Keras での重みクラスタリングの例

<table class="tfo-notebook-buttons" align="left">
  <td><a target="_blank" href="https://www.tensorflow.org/model_optimization/guide/clustering/clustering_example"><img src="https://www.tensorflow.org/images/tf_logo_32px.png">TensorFlow.orgで表示</a></td>
  <td><a target="_blank" href="https://colab.research.google.com/github/tensorflow/docs-l10n/blob/master/site/ja/model_optimization/guide/clustering/clustering_example.ipynb"><img src="https://www.tensorflow.org/images/colab_logo_32px.png">Google Colabで実行</a></td>
  <td><a target="_blank" href="https://github.com/tensorflow/docs-l10n/blob/master/site/ja/model_optimization/guide/clustering/clustering_example.ipynb"><img src="https://www.tensorflow.org/images/GitHub-Mark-32px.png">      GitHub でソースを表示</a></td>
  <td><a href="https://storage.googleapis.com/tensorflow_docs/docs-l10n/site/ja/model_optimization/guide/clustering/clustering_example.ipynb"><img src="https://www.tensorflow.org/images/download_logo_32px.png">ノートブックをダウンロード</a></td>
</table>

## 概要

TensorFlow Model Optimization ツールキットの一部である*重みクラスタリング*のエンドツーエンドの例へようこそ。

### その他のページ

重みクラスタリングの紹介、およびクラスタリングを使用すべきかどうかの判定（サポート情報も含む）については、[概要ページ](https://www.tensorflow.org/model_optimization/guide/clustering)をご覧ください。

ユースケースに合った API を素早く特定するには（16 個のクラスタでモデルを完全クラスタ化するケースを超える内容）、[総合ガイド](https://www.tensorflow.org/model_optimization/guide/clustering/clustering_comprehensive_guide)をご覧ください。

### 内容

チュートリアルでは、次について説明しています。

1. MNIST データセットの `tf.keras` モデルを最初からトレーニングする
2. 重みクラスタリング API を適用してモデルを微調整し、精度を確認する
3. クラスタリングによって 6 倍小さな TF および TFLite モデルを作成する
4. 重みクラスタリングとポストトレーニング量子化を組み合わせて、8 倍小さな TFLite モデルを作成する
5. TF から TFLite への精度の永続性を確認する

## セットアップ

この Jupyter ノートブックは、ローカルの [virtualenv](https://www.tensorflow.org/install/pip?lang=python3#2.-create-a-virtual-environment-recommended) または [Colab](https://colab.sandbox.google.com/) で実行できます。依存関係のセットアップに関する詳細は、[インストールガイド](https://www.tensorflow.org/model_optimization/guide/install)をご覧ください。 

In [2]:
! pip install -q tensorflow-model-optimization

In [3]:
import tensorflow as tf
from tensorflow import keras

import numpy as np
import tempfile
import zipfile
import os

## クラスタを使用せずに、MNIST の tf.keras モデルをトレーニングする

In [4]:
# Load MNIST dataset
mnist = keras.datasets.mnist
(train_images, train_labels), (test_images, test_labels) = mnist.load_data()

# Normalize the input image so that each pixel value is between 0 to 1.
train_images = train_images / 255.0
test_images  = test_images / 255.0

# Define the model architecture.
model = keras.Sequential([
    keras.layers.InputLayer(input_shape=(28, 28)),
    keras.layers.Reshape(target_shape=(28, 28, 1)),
    keras.layers.Conv2D(filters=12, kernel_size=(3, 3), activation=tf.nn.relu),
    keras.layers.MaxPooling2D(pool_size=(2, 2)),
    keras.layers.Flatten(),
    keras.layers.Dense(10)
])

# Train the digit classification model
model.compile(optimizer='adam',
              loss=tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True),
              metrics=['accuracy'])

model.fit(
    train_images,
    train_labels,
    validation_split=0.1,
    epochs=10
)

Epoch 1/10


   1/1688 [..............................] - ETA: 1:09:26 - loss: 2.3776 - accuracy: 0.0938

  24/1688 [..............................] - ETA: 3s - loss: 2.1879 - accuracy: 0.3025     

  49/1688 [..............................] - ETA: 3s - loss: 2.0258 - accuracy: 0.4017

  74/1688 [>.............................] - ETA: 3s - loss: 1.8641 - accuracy: 0.4692

...

1600/1688 [===========================>..] - ETA: 0s - loss: 0.0371 - accuracy: 0.9888

1625/1688 [===========================>..] - ETA: 0s - loss: 0.0371 - accuracy: 0.9888

1651/1688 [============================>.] - ETA: 0s - loss: 0.0372 - accuracy: 0.9888

1677/1688 [============================>.] - ETA: 0s - loss: 0.0372 - accuracy: 0.9888

1688/1688 [==============================] - 4s 2ms/step - loss: 0.0372 - accuracy: 0.9888 - val_loss: 0.0684 - val_accuracy: 0.9818


### ベースラインモデルを評価して後で使用できるように保存する

In [5]:
_, baseline_model_accuracy = model.evaluate(
    test_images, test_labels, verbose=0)

print('Baseline test accuracy:', baseline_model_accuracy)

_, keras_file = tempfile.mkstemp('.h5')
print('Saving model to: ', keras_file)
tf.keras.models.save_model(model, keras_file, include_optimizer=False)

Baseline test accuracy: 0.9789999723434448
Saving model to:  /tmp/tmp8m1tzkhh.h5


## クラスタを使ってトレーニング済みのモデルを微調整する

`cluster_weights()` API をトレーニング済みのモデル全体に適用し、十分な精度を維持しながら zip 適用後のモデル縮小の効果を実演します。ユースケースに応じた精度と圧縮率のバランスについては、[総合ガイド](https://www.tensorflow.org/model_optimization/guide/clustering/clustering_comprehensive_guide)のレイヤー別の例をご覧ください。


### モデルを定義してクラスタリング API を適用する

クラスタリング API にモデルを渡す前に、必ずトレーニングを実行し、許容できる精度が備わっていることを確認してください。

In [6]:
import tensorflow_model_optimization as tfmot

cluster_weights = tfmot.clustering.keras.cluster_weights
CentroidInitialization = tfmot.clustering.keras.CentroidInitialization

clustering_params = {
  'number_of_clusters': 16,
  'cluster_centroids_init': CentroidInitialization.LINEAR
}

# Cluster a whole model
clustered_model = cluster_weights(model, **clustering_params)

# Use smaller learning rate for fine-tuning clustered model
opt = tf.keras.optimizers.Adam(learning_rate=1e-5)

clustered_model.compile(
  loss=tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True),
  optimizer=opt,
  metrics=['accuracy'])

clustered_model.summary()

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
cluster_reshape (ClusterWeig (None, 28, 28, 1)         0         
_________________________________________________________________
cluster_conv2d (ClusterWeigh (None, 26, 26, 12)        136       
_________________________________________________________________
cluster_max_pooling2d (Clust (None, 13, 13, 12)        0         
_________________________________________________________________
cluster_flatten (ClusterWeig (None, 2028)              0         
_________________________________________________________________
cluster_dense (ClusterWeight (None, 10)                20306     
Total params: 20,442
Trainable params: 54
Non-trainable params: 20,388
_________________________________________________________________


### モデルを微調整し、ベースラインに対する精度を評価する

1 エポック、クラスタでモデルを微調整します。

In [7]:
# Fine-tune model
clustered_model.fit(
  train_images,
  train_labels,
  batch_size=500,
  epochs=1,
  validation_split=0.1)

  1/108 [..............................] - ETA: 47s - loss: 0.0911 - accuracy: 0.9680

 17/108 [===>..........................] - ETA: 0s - loss: 0.0690 - accuracy: 0.9767 

 33/108 [========>.....................] - ETA: 0s - loss: 0.0675 - accuracy: 0.9771

 49/108 [============>.................] - ETA: 0s - loss: 0.0677 - accuracy: 0.9768

 65/108 [=================>............] - ETA: 0s - loss: 0.0681 - accuracy: 0.9768

 81/108 [=====================>........] - ETA: 0s - loss: 0.0683 - accuracy: 0.9768

 97/108 [=========================>....] - ETA: 0s - loss: 0.0683 - accuracy: 0.9769

108/108 [==============================] - 1s 6ms/step - loss: 0.0683 - accuracy: 0.9770 - val_loss: 0.0977 - val_accuracy: 0.9747


この例では、ベースラインと比較し、クラスタリング後のテスト精度に最小限の損失があります。

In [8]:
_, clustered_model_accuracy = clustered_model.evaluate(
  test_images, test_labels, verbose=0)

print('Baseline test accuracy:', baseline_model_accuracy)
print('Clustered test accuracy:', clustered_model_accuracy)

Baseline test accuracy: 0.9789999723434448
Clustered test accuracy: 0.9702000021934509


## クラスタリングによって **6 倍**小さなモデルを作成する

<code>strip_clustering</code> と標準圧縮アルゴリズム（gzip など）の適用は、クラスタリングの圧縮のメリットを確認する上で必要です。

まず、TensorFlow の圧縮可能なモデルを作成します。ここで、`strip_clustering` は、クラスタリングがトレーニング中にのみ必要とするすべての変数（クラスタの重心とインデックスを格納する `tf.Variable` など）を除去します。そうしない場合、推論中にモデルサイズが増加してしまいます。

In [9]:
final_model = tfmot.clustering.keras.strip_clustering(clustered_model)

_, clustered_keras_file = tempfile.mkstemp('.h5')
print('Saving clustered model to: ', clustered_keras_file)
tf.keras.models.save_model(final_model, clustered_keras_file, 
                           include_optimizer=False)

Saving clustered model to:  /tmp/tmpz9c4ugbj.h5


次に、TFLite の圧縮可能なモデルを作成します。クラスタモデルをターゲットバックエンドで実行可能な形式に変換できます。TensorFlow Lite は、モバイルデバイスにデプロイするために使用できる例です。

In [10]:
clustered_tflite_file = '/tmp/clustered_mnist.tflite'
converter = tf.lite.TFLiteConverter.from_keras_model(final_model)
tflite_clustered_model = converter.convert()
with open(clustered_tflite_file, 'wb') as f:
  f.write(tflite_clustered_model)
print('Saved clustered TFLite model to:', clustered_tflite_file)

INFO:tensorflow:Assets written to: /tmp/tmp41s2kzub/assets


Saved clustered TFLite model to: /tmp/clustered_mnist.tflite


実際に gzip でモデルを圧縮し、zip 圧縮されたサイズを測定するヘルパー関数を定義します。

In [11]:
def get_gzipped_model_size(file):
  # It returns the size of the gzipped model in bytes.
  import os
  import zipfile

  _, zipped_file = tempfile.mkstemp('.zip')
  with zipfile.ZipFile(zipped_file, 'w', compression=zipfile.ZIP_DEFLATED) as f:
    f.write(file)

  return os.path.getsize(zipped_file)

比較して、モデルがクラスタリングによって **6 倍**小さくなっていることを確認します。

In [12]:
print("Size of gzipped baseline Keras model: %.2f bytes" % (get_gzipped_model_size(keras_file)))
print("Size of gzipped clustered Keras model: %.2f bytes" % (get_gzipped_model_size(clustered_keras_file)))
print("Size of gzipped clustered TFlite model: %.2f bytes" % (get_gzipped_model_size(clustered_tflite_file)))

Size of gzipped baseline Keras model: 78047.00 bytes
Size of gzipped clustered Keras model: 12419.00 bytes
Size of gzipped clustered TFlite model: 11920.00 bytes


## 重みクラスタリングとポストトレーニング量子化を組み合わせて、**8 倍**小さな TFLite モデルを作成する

さらにメリットを得るために、ポストトレーニング量子化をクラスタモデルに適用できます。

In [13]:
converter = tf.lite.TFLiteConverter.from_keras_model(final_model)
converter.optimizations = [tf.lite.Optimize.DEFAULT]
tflite_quant_model = converter.convert()

_, quantized_and_clustered_tflite_file = tempfile.mkstemp('.tflite')

with open(quantized_and_clustered_tflite_file, 'wb') as f:
  f.write(tflite_quant_model)

print('Saved quantized and clustered TFLite model to:', quantized_and_clustered_tflite_file)
print("Size of gzipped baseline Keras model: %.2f bytes" % (get_gzipped_model_size(keras_file)))
print("Size of gzipped clustered and quantized TFlite model: %.2f bytes" % (get_gzipped_model_size(quantized_and_clustered_tflite_file)))

INFO:tensorflow:Assets written to: /tmp/tmpg3y6r2ll/assets


INFO:tensorflow:Assets written to: /tmp/tmpg3y6r2ll/assets


Saved quantized and clustered TFLite model to: /tmp/tmp6p9j3n3w.tflite
Size of gzipped baseline Keras model: 78047.00 bytes
Size of gzipped clustered and quantized TFlite model: 9045.00 bytes


## TF から TFLite への精度の永続性を確認する

テストデータセットで TFLite モデルを評価するヘルパー関数を定義します。

In [14]:
def eval_model(interpreter):
  input_index = interpreter.get_input_details()[0]["index"]
  output_index = interpreter.get_output_details()[0]["index"]

  # Run predictions on every image in the "test" dataset.
  prediction_digits = []
  for i, test_image in enumerate(test_images):
    if i % 1000 == 0:
      print('Evaluated on {n} results so far.'.format(n=i))
    # Pre-processing: add batch dimension and convert to float32 to match with
    # the model's input data format.
    test_image = np.expand_dims(test_image, axis=0).astype(np.float32)
    interpreter.set_tensor(input_index, test_image)

    # Run inference.
    interpreter.invoke()

    # Post-processing: remove batch dimension and find the digit with highest
    # probability.
    output = interpreter.tensor(output_index)
    digit = np.argmax(output()[0])
    prediction_digits.append(digit)

  print('\n')
  # Compare prediction results with ground truth labels to calculate accuracy.
  prediction_digits = np.array(prediction_digits)
  accuracy = (prediction_digits == test_labels).mean()
  return accuracy

クラスタ化および量子化されたモデルを評価し、TensorFlow の精度が TFLite バックエンドに持続することを確認します。

In [15]:
interpreter = tf.lite.Interpreter(model_content=tflite_quant_model)
interpreter.allocate_tensors()

test_accuracy = eval_model(interpreter)

print('Clustered and quantized TFLite test_accuracy:', test_accuracy)
print('Clustered TF test accuracy:', clustered_model_accuracy)

Evaluated on 0 results so far.


Evaluated on 1000 results so far.


Evaluated on 2000 results so far.


Evaluated on 3000 results so far.


Evaluated on 4000 results so far.


...

Evaluated on 6000 results so far.


Evaluated on 7000 results so far.


Evaluated on 8000 results so far.


Evaluated on 9000 results so far.




Clustered and quantized TFLite test_accuracy: 0.9698
Clustered TF test accuracy: 0.9702000021934509


## まとめ

このチュートリアルでは、TensorFlow Model Optimization Toolkit API を使用してクラスタモデルを作成する方法を確認しました。より具体的には、精度の違いを最小限に抑えて MNIST の 8 倍の小さいモデルを作成する、エンドツーエンドの例を確認しました。この新しい機能を試すことをお勧めします。これは、リソースに制約のある環境でのデプロイに特に重要な機能です。
